In [1]:
# Importing necessary packages
import numpy as np
import pandas as pd
import networkx as nx
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import json
from dask import delayed, compute
import dask
from gensim.models import Word2Vec
import networkx as nx
from node2vec import Node2Vec
import pickle
import json

In [5]:
# Correctly loading JSON data and handling it based on its structure
with open('upd_article_url.json') as f:
    data = json.load(f)
if isinstance(data, list):
    url_1 = pd.DataFrame(data)
elif isinstance(data, dict):
    url_1 = pd.DataFrame.from_dict(data, orient='index')

with open('upd_article_url_1.json') as f:
    data = json.load(f)
if isinstance(data, list):
    url_2 = pd.DataFrame(data)
elif isinstance(data, dict):
    url_2 = pd.DataFrame.from_dict(data, orient='index')
with open('upd_article_url_2.json') as f:
    data = json.load(f)
if isinstance(data, list):
    url_3 = pd.DataFrame(data)
elif isinstance(data, dict):
    url_3 = pd.DataFrame.from_dict(data, orient='index')
with open('upd_article_url_3.json') as f:
    data = json.load(f)
if isinstance(data, list):
    url_4 = pd.DataFrame(data)
elif isinstance(data, dict):
    url_4 = pd.DataFrame.from_dict(data, orient='index')

In [6]:
# Combining all the dataframes loaded
url_dt = pd.concat([url_1, url_2, url_3, url_4], axis=0)
# Removing duplicates from combined dataframe with duplicate url values being removed
url_dt.drop_duplicates(subset=['url'], inplace = True)

In [7]:
# Shape of combined dataframe
url_dt.shape

(40630, 2)

In [8]:
# Combined tokenized dataframe 
df = pd.read_csv('final.csv')
df.head(10)

Unnamed: 0               name  \
0           0        Sarah Perez   
1           1  Dr.Robert Mueller   
2           2        Sarah Perez   
3           3  Dr.Robert Mueller   
4           4      Jeffrey Price   
5           5  Dr.Michael Romero   
6           6       Morgan Smith   
7           7        Sarah Perez   
8           8      Jeffrey Price   
9           9        Sarah Perez   

                                                 url  \
0  https://techcrunch.com/2012/12/04/google-annou...   
1  https://www.nytimes.com/2023/07/11/us/politics...   
2  https://techcrunch.com/2020/05/06/facebook-exo...   
3  https://www.nytimes.com/2021/05/27/health/wuha...   
4  https://hakaimagazine.com/news/hawksbill-turtl...   
5  http://www.tribune242.com/news/2014/jan/09/don...   
6  https://slate.com/news-and-politics/2007/10/wh...   
7  https://techcrunch.com/2015/07/06/pembient-co-...   
8  https://www.nationalgeographic.com/animals/art...   
9  https://www.khq.com/news/gonzaga-nursing-stude...   

                                             content  \
0  TechCrunch plus-bold TechCrunch Open Navigatio...   
1  Skip to content Skip to site index Politics To...   
2  TechCrunch plus-bold TechCrunch Open Navigatio...   
3  Skip to content Skip to site index Health Toda...   
4  Hakai Magazine Skip to content Coastal science...   
5  The Tribune Jump to content Login or Sign up H...   
6  Skip to the content Slate Shop Daily Quiz News...   
7  TechCrunch plus-bold TechCrunch Open Navigatio...   
8  Skip to content Newsletters Subscribe Menu Ani...   
9  Skip to main content You are the owner of this...   

                                              tokens  
0  ['tech', '##cr', '##un', '##ch', 'plus', '-', ...  
1  ['skip', 'to', 'content', 'skip', 'to', 'site'...  
2  ['tech', '##cr', '##un', '##ch', 'plus', '-', ...  
3  ['skip', 'to', 'content', 'skip', 'to', 'site'...  
4  ['ha', '##kai', 'magazine', 'skip', 'to', 'con...  
5  ['the', 'tribune', 'jump', 'to', 'content', 'l...  
6  ['skip', 'to', 'the', 'content', 'slate', 'sho...  
7  ['tech', '##cr', '##un', '##ch', 'plus', '-', ...  
8  ['skip', 'to', 'content', 'newsletter', '##s',...  
9  ['skip', 'to', 'main', 'content', 'you', 'are'...

In [9]:
# Dropping rows with same content
df.drop_duplicates(subset=['content'])

Unnamed: 0               name  \
0               0        Sarah Perez   
1               1  Dr.Robert Mueller   
2               2        Sarah Perez   
3               3  Dr.Robert Mueller   
4               4      Jeffrey Price   
...           ...                ...   
46560       46560       Joseph Greer   
46561       46561        James Brown   
46562       46562      Erik Thompson   
46563       46563      Matthew Scott   
46566       46566      Matthew Scott   

                                                     url  \
0      https://techcrunch.com/2012/12/04/google-annou...   
1      https://www.nytimes.com/2023/07/11/us/politics...   
2      https://techcrunch.com/2020/05/06/facebook-exo...   
3      https://www.nytimes.com/2021/05/27/health/wuha...   
4      https://hakaimagazine.com/news/hawksbill-turtl...   
...                                                  ...   
46560  https://cw39.com/news/local/watch-live-harris-...   
46561  https://www.mirror.co.uk/news/world-news/fugit...   
46562  https://www.breakingbelizenews.com/2022/08/25/...   
46563  https://www.somersetlive.co.uk/news/local-news...   
46566  https://www.dorsetecho.co.uk/news/18305867.sco...   

                                                 content  \
0      TechCrunch plus-bold TechCrunch Open Navigatio...   
1      Skip to content Skip to site index Politics To...   
2      TechCrunch plus-bold TechCrunch Open Navigatio...   
3      Skip to content Skip to site index Health Toda...   
4      Hakai Magazine Skip to content Coastal science...   
...                                                  ...   
46560  Skip to content CW39 Houston Houston 58° WATCH...   
46561  US Edition ▼ US Edition UK Edition Irish Mirro...   
46562  Submit News 501-666-6726 [email protected] Hom...   
46563  somersetlive Load mobile navigation News Lates...   
46566  Newsletters Jobs Homes Motoring Local Listings...   

                                                  tokens  
0      ['tech', '##cr', '##un', '##ch', 'plus', '-', ...  
1      ['skip', 'to', 'content', 'skip', 'to', 'site'...  
2      ['tech', '##cr', '##un', '##ch', 'plus', '-', ...  
3      ['skip', 'to', 'content', 'skip', 'to', 'site'...  
4      ['ha', '##kai', 'magazine', 'skip', 'to', 'con...  
...                                                  ...  
46560  ['skip', 'to', 'content', 'cw', '##39', 'houst...  
46561  ['us', 'edition', '[UNK]', 'us', 'edition', 'u...  
46562  ['submit', 'news', '501', '-', '66', '##6', '-...  
46563  ['somerset', '##li', '##ve', 'load', 'mobile',...  
46566  ['newsletter', '##s', 'jobs', 'homes', 'motor'...  

[40245 rows x 5 columns]

In [10]:
# Shape of combined dataframe with relevant content after duplicate removal
df.shape

(46567, 5)

In [11]:
# Shape of combined url dataframe after duplicate removal
url_dt.shape

(40630, 2)

In [12]:
# Merging the combined url and combined content dataframes using inner join on name and url columns
df_up = df.merge(url_dt, on = ['name','url'], how = 'inner')
# Evaluating the shape of the dataframe
df_up.shape

(31273, 5)

In [13]:
# Checking the columns in the final combined dataframe
df_up.columns

Index(['Unnamed: 0', 'name', 'url', 'content', 'tokens'], dtype='object')

In [14]:
# Dropping irrelevant columns from the dataframe
df_up.drop('Unnamed: 0',axis = 1, inplace = True)
df_up.head(5)

name                                                url  \
0  Dr.Michael Romero  http://www.tribune242.com/news/2014/jan/09/don...   
1       Morgan Smith  https://slate.com/news-and-politics/2007/10/wh...   
2      Jeffrey Price  https://www.nationalgeographic.com/animals/art...   
3        Sarah Perez  https://www.khq.com/news/gonzaga-nursing-stude...   
4      Jeffrey Price  https://www.unionleader.com/news/back_page/jef...   

                                             content  \
0  The Tribune Jump to content Login or Sign up H...   
1  Skip to the content Slate Shop Daily Quiz News...   
2  Skip to content Newsletters Subscribe Menu Ani...   
3  Skip to main content You are the owner of this...   
4  Skip to main content You have permission to ed...   

                                              tokens  
0  ['the', 'tribune', 'jump', 'to', 'content', 'l...  
1  ['skip', 'to', 'the', 'content', 'slate', 'sho...  
2  ['skip', 'to', 'content', 'newsletter', '##s',...  
3  ['skip', 'to', 'main', 'content', 'you', 'are'...  
4  ['skip', 'to', 'main', 'content', 'you', 'have...

In [15]:
# Creating a dummy variable indicating that value in name column exists in content with 1 indicating existent and 0 indicating non-existent
df_up['flag'] = df_up.apply(lambda row: 1 if str(row['name']).lower() in str(row['content']).lower() else 0, axis=1)
df_up.head(5)

name                                                url  \
0  Dr.Michael Romero  http://www.tribune242.com/news/2014/jan/09/don...   
1       Morgan Smith  https://slate.com/news-and-politics/2007/10/wh...   
2      Jeffrey Price  https://www.nationalgeographic.com/animals/art...   
3        Sarah Perez  https://www.khq.com/news/gonzaga-nursing-stude...   
4      Jeffrey Price  https://www.unionleader.com/news/back_page/jef...   

                                             content  \
0  The Tribune Jump to content Login or Sign up H...   
1  Skip to the content Slate Shop Daily Quiz News...   
2  Skip to content Newsletters Subscribe Menu Ani...   
3  Skip to main content You are the owner of this...   
4  Skip to main content You have permission to ed...   

                                              tokens  flag  
0  ['the', 'tribune', 'jump', 'to', 'content', 'l...     0  
1  ['skip', 'to', 'the', 'content', 'slate', 'sho...     1  
2  ['skip', 'to', 'content', 'newsletter', '##s',...     0  
3  ['skip', 'to', 'main', 'content', 'you', 'are'...     1  
4  ['skip', 'to', 'main', 'content', 'you', 'have...     0

In [16]:
# Creating another dummy variable in which 1 indicates the term wildlife is in content and 0 indicating wildlife is absent from content
df_up['flag_1'] = df_up.apply(lambda row: 1 if 'wildlife' in str(row['content']).lower() else 0, axis=1)
df_up.head(5)

name                                                url  \
0  Dr.Michael Romero  http://www.tribune242.com/news/2014/jan/09/don...   
1       Morgan Smith  https://slate.com/news-and-politics/2007/10/wh...   
2      Jeffrey Price  https://www.nationalgeographic.com/animals/art...   
3        Sarah Perez  https://www.khq.com/news/gonzaga-nursing-stude...   
4      Jeffrey Price  https://www.unionleader.com/news/back_page/jef...   

                                             content  \
0  The Tribune Jump to content Login or Sign up H...   
1  Skip to the content Slate Shop Daily Quiz News...   
2  Skip to content Newsletters Subscribe Menu Ani...   
3  Skip to main content You are the owner of this...   
4  Skip to main content You have permission to ed...   

                                              tokens  flag  flag_1  
0  ['the', 'tribune', 'jump', 'to', 'content', 'l...     0       1  
1  ['skip', 'to', 'the', 'content', 'slate', 'sho...     1       1  
2  ['skip', 'to', 'content', 'newsletter', '##s',...     0       1  
3  ['skip', 'to', 'main', 'content', 'you', 'are'...     1       0  
4  ['skip', 'to', 'main', 'content', 'you', 'have...     0       0

In [17]:
# Creating another dummy variable in which 1 indicates the term trafficking is in content and 0 indicating trafficking is absent from content
df_up['flag_2'] = df_up.apply(lambda row: 1 if 'trafficking' in str(row['content']).lower() else 0, axis=1)
df_up.head(5)

name                                                url  \
0  Dr.Michael Romero  http://www.tribune242.com/news/2014/jan/09/don...   
1       Morgan Smith  https://slate.com/news-and-politics/2007/10/wh...   
2      Jeffrey Price  https://www.nationalgeographic.com/animals/art...   
3        Sarah Perez  https://www.khq.com/news/gonzaga-nursing-stude...   
4      Jeffrey Price  https://www.unionleader.com/news/back_page/jef...   

                                             content  \
0  The Tribune Jump to content Login or Sign up H...   
1  Skip to the content Slate Shop Daily Quiz News...   
2  Skip to content Newsletters Subscribe Menu Ani...   
3  Skip to main content You are the owner of this...   
4  Skip to main content You have permission to ed...   

                                              tokens  flag  flag_1  flag_2  
0  ['the', 'tribune', 'jump', 'to', 'content', 'l...     0       1       0  
1  ['skip', 'to', 'the', 'content', 'slate', 'sho...     1       1       1  
2  ['skip', 'to', 'content', 'newsletter', '##s',...     0       1       0  
3  ['skip', 'to', 'main', 'content', 'you', 'are'...     1       0       0  
4  ['skip', 'to', 'main', 'content', 'you', 'have...     0       0       1

In [18]:
# Creating a variable which combines the three dummy variables values
df_up['fin_flag'] = df_up['flag']+df_up['flag_2']+df_up['flag_2']
# Filtering the dataframe for rows containing any of wildlife, trafficking, or name in content 
df_up[df_up.fin_flag >=1]

name                                                url  \
1            Morgan Smith  https://slate.com/news-and-politics/2007/10/wh...   
3             Sarah Perez  https://www.khq.com/news/gonzaga-nursing-stude...   
4           Jeffrey Price  https://www.unionleader.com/news/back_page/jef...   
10     Christopher Newman  https://theconversation.com/pangolin-illegal-m...   
12     Christopher Newman  https://theecologist.org/2016/sep/20/whats-nam...   
...                   ...                                                ...   
31262        Nancy Willis  https://www.pressdemocrat.com/article/napa/nap...   
31264       Matthew Scott  https://www.nytimes.com/2017/12/05/science/sum...   
31266        Joseph Greer  https://cw39.com/news/local/watch-live-harris-...   
31267         James Brown  https://www.mirror.co.uk/news/world-news/fugit...   
31268       Erik Thompson  https://www.breakingbelizenews.com/2022/08/25/...   

                                                 content  \
1      Skip to the content Slate Shop Daily Quiz News...   
3      Skip to main content You are the owner of this...   
4      Skip to main content You have permission to ed...   
10     Menu Close Home Podcasts COVID-19 Arts Busines...   
12     Skip to main content Menu Breadcrumb Home Comm...   
...                                                  ...   
31262  Skip to content Skip to footer Show Menu Hide ...   
31264  Skip to content Skip to site index Science Tod...   
31266  Skip to content CW39 Houston Houston 58° WATCH...   
31267  US Edition ▼ US Edition UK Edition Irish Mirro...   
31268  Submit News 501-666-6726 [email protected] Hom...   

                                                  tokens  flag  flag_1  \
1      ['skip', 'to', 'the', 'content', 'slate', 'sho...     1       1   
3      ['skip', 'to', 'main', 'content', 'you', 'are'...     1       0   
4      ['skip', 'to', 'main', 'content', 'you', 'have...     0       0   
10     ['menu', 'close', 'home', 'podcast', '##s', 'c...     0       1   
12     ['skip', 'to', 'main', 'content', 'menu', 'bre...     0       1   
...                                                  ...   ...     ...   
31262  ['skip', 'to', 'content', 'skip', 'to', 'foot'...     1       0   
31264  ['skip', 'to', 'content', 'skip', 'to', 'site'...     1       1   
31266  ['skip', 'to', 'content', 'cw', '##39', 'houst...     1       0   
31267  ['us', 'edition', '[UNK]', 'us', 'edition', 'u...     1       0   
31268  ['submit', 'news', '501', '-', '66', '##6', '-...     0       0   

       flag_2  fin_flag  
1           1         3  
3           0         1  
4           1         2  
10          1         2  
12          1         2  
...       ...       ...  
31262       0         1  
31264       0         1  
31266       0         1  
31267       0         1  
31268       1         2  

[14918 rows x 8 columns]

In [19]:
# Creating another dataframe in which rows indicate that content variable has any of wildlife, trafficking, or name in it
df_final = df_up[df_up.fin_flag > 0].copy()

In [162]:
df_final.head(5)

name  \
1         Morgan Smith   
3          Sarah Perez   
4        Jeffrey Price   
10  Christopher Newman   
12  Christopher Newman   

                                                                                                                                                          url  \
1                                      https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3               https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
4   https://www.unionleader.com/news/back_page/jeffrey-epstein-s-islands-stir-doubts-over-125-million-price/article_3680bbc9-dd4a-5b24-91f4-cf5fa169f680.html   
10                                            https://theconversation.com/pangolin-illegal-medicine-trade-threatens-these-scaly-mammals-with-extinction-33817   
12                                                        https://theecologist.org/2016/sep/20/whats-name-control-chinas-wildlife-trade-law-must-keep-science   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [22]:
pd.set_option('display.max_colwidth', None)  # For pandas versions < 1.0
#pd.set_option('display.max_colwidth', 0)  # For pandas versions >= 1.0
#df_final.content

In [23]:
def optimized_extract_relevant_lines(df):
    # Preparing a list to hold the results
    relevant_contents = []

    # Iterating through the DataFrame rows
    for _, row in df.iterrows():
        name, content = row['name'], row['content']
        sentences = content.split('.')
        
        found_index = -1
        for i, sentence in enumerate(sentences):
            if name in sentence:
                found_index = i
                break  # Stop at the first occurrence
        
        # If the name was found within the content
        if found_index != -1:
            # Extracting the relevant sentences
            start_index = max(found_index - 6, 0)  # Ensure we don't go beyond the start of the list
            end_index = min(found_index + 7, len(sentences))  # Ensure we don't go beyond the end of the list, +4 because range is exclusive and we want 3 sentences after the found index
            relevant_sentence = '. '.join(sentences[start_index:end_index]).strip() + '.'
        else:
            relevant_sentence = ''

        relevant_contents.append(relevant_sentence)
    
    return relevant_contents


# Adding the extracted relevant sentences to the DataFrame
df_final['relevant_content'] = optimized_extract_relevant_lines(df_final)

In [24]:
df_final.head()

name  \
1         Morgan Smith   
3          Sarah Perez   
4        Jeffrey Price   
10  Christopher Newman   
12  Christopher Newman   

                                                                                                                                                          url  \
1                                      https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3               https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
4   https://www.unionleader.com/news/back_page/jeffrey-epstein-s-islands-stir-doubts-over-125-million-price/article_3680bbc9-dd4a-5b24-91f4-cf5fa169f680.html   
10                                            https://theconversation.com/pangolin-illegal-medicine-trade-threatens-these-scaly-mammals-with-extinction-33817   
12                                                        https://theecologist.org/2016/sep/20/whats-name-control-chinas-wildlife-trade-law-must-keep-science   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [25]:
df_rep = df_final[['name','url','relevant_content']].copy()

In [26]:
df_rep['relevant_content']=df_rep['relevant_content'].replace('', np.NaN)
df_rep_cleaned = df_rep.dropna(subset=['relevant_content'])
df_rep_cleaned.shape

(6790, 3)

In [27]:
df_rep_cleaned.head(5)

name  \
1     Morgan Smith   
3      Sarah Perez   
17     Jeff Wright   
19   Michael Kelly   
22  Michael Bishop   

                                                                                                                                              url  \
1                          https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3   https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
17                                                https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
19                                                  https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
22                                             https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              relevant_content  
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

In [28]:
#df_rep_cleaned.to_json('exp_fin.json', orient='records', lines=True)

In [29]:
from transformers import AutoTokenizer, AutoModel
import torch
import numpy as np
from sklearn.cluster import KMeans
import os

os.environ['TOKENIZERS_PARALLELISM'] = 'false'

# Load model and tokenizer
tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")
model = AutoModel.from_pretrained("distilbert-base-uncased")

# Function to generate embeddings
def get_embeddings(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    outputs = model(**inputs)
    return outputs.last_hidden_state.mean(dim=1).detach().cpu().numpy()

# Example usage
texts = df_rep_cleaned['relevant_content'].tolist()
embeddings = np.vstack([get_embeddings(text) for text in texts])

# Clustering embeddings
kmeans = KMeans(n_clusters=5, random_state=42).fit(embeddings)

In [30]:
from transformers import pipeline
classifier=pipeline('zero-shot-classification',model='facebook/bart-large-mnli')
texts=df_rep_cleaned['relevant_content']
labels=['wildlife trafficking', 'human trafficking','drug trafficking','not wildlife trafficking']
def classify_text(text):
    result=classifier(text, candidate_labels=labels,multi_label=True)
    predicted_labels=result['labels']
    scores=result['scores']
    return predicted_labels,scores

In [38]:
df_sevenk=pd.read_json('seven_k_rows_scores_labels.json',lines=True)
df_sevenk

name  \
0       Morgan Smith   
1        Sarah Perez   
2        Jeff Wright   
3      Michael Kelly   
4     Michael Bishop   
...              ...   
6785   Matthew Scott   
6786    Nancy Willis   
6787   Matthew Scott   
6788    Joseph Greer   
6789     James Brown   

                                                                                                                                                    url  \
0                                https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
1         https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
2                                                       https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
3                                                         https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
4                                                    https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   
...                                                                                                                                                 ...   
6785                                                              https://www.nationaltribune.com.au/wa-man-jailed-after-3kg-of-meth-found-in-backpack/   
6786                                             https://www.pressdemocrat.com/article/napa/napa-panel-addresses-artists-need-for-space-and-visibility/   
6787                                                                                    https://www.nytimes.com/2017/12/05/science/sumatran-tigers.html   
6788  https://cw39.com/news/local/watch-live-harris-county-sheriffs-office-us-marshals-capture-most-wanted-fugitive-charged-in-girlfriends-2006-murder/   
6789                                                          https://www.mirror.co.uk/news/world-news/fugitive-unimpressed-smiling-james-brown-7157557   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [39]:
import spacy
nlp=spacy.load('en_core_web_sm')
def extract_entities(text):
    # Process the text through the spaCy pipeline
    doc = nlp(text)
    # Extract entities and their labels
    entities = [(ent.text, ent.label_) for ent in doc.ents]
    return entities
df_sevenk['entities'] = df_sevenk['relevant_content'].apply(extract_entities)

In [40]:
df_sevenk

name  \
0       Morgan Smith   
1        Sarah Perez   
2        Jeff Wright   
3      Michael Kelly   
4     Michael Bishop   
...              ...   
6785   Matthew Scott   
6786    Nancy Willis   
6787   Matthew Scott   
6788    Joseph Greer   
6789     James Brown   

                                                                                                                                                    url  \
0                                https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
1         https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
2                                                       https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
3                                                         https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
4                                                    https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   
...                                                                                                                                                 ...   
6785                                                              https://www.nationaltribune.com.au/wa-man-jailed-after-3kg-of-meth-found-in-backpack/   
6786                                             https://www.pressdemocrat.com/article/napa/napa-panel-addresses-artists-need-for-space-and-visibility/   
6787                                                                                    https://www.nytimes.com/2017/12/05/science/sumatran-tigers.html   
6788  https://cw39.com/news/local/watch-live-harris-county-sheriffs-office-us-marshals-capture-most-wanted-fugitive-charged-in-girlfriends-2006-murder/   
6789                                                          https://www.mirror.co.uk/news/world-news/fugitive-unimpressed-smiling-james-brown-7157557   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [41]:
#df_sevenk.to_json('tokenized_ner.json',orient='records',lines=True)

In [69]:
lst=df_rep_cleaned['relevant_content'].to_list()
lst1=[]
for i in range(0,1000):
    tupped=classify_text(lst[i])
    print(tupped)
    lst1.append(tupped)
#results=df_rep_cleaned['relevant_content'].apply(lambda x: classify_text(x))
#df_rep_cleaned['predicted_labels'],df_rep_cleaned['scores']=zip(*results)

(['wildlife trafficking', 'not wildlife trafficking'], [0.25968116521835327, 0.012058272026479244])
(['not wildlife trafficking', 'wildlife trafficking'], [0.0990157499909401, 0.039518970996141434])
(['wildlife trafficking', 'not wildlife trafficking'], [0.0292100477963686, 0.009051206521689892])
(['wildlife trafficking', 'not wildlife trafficking'], [0.1545344889163971, 0.04707414284348488])
(['not wildlife trafficking', 'wildlife trafficking'], [0.08096851408481598, 0.03361132740974426])
(['wildlife trafficking', 'not wildlife trafficking'], [0.25151917338371277, 0.018917076289653778])
(['not wildlife trafficking', 'wildlife trafficking'], [0.022322705015540123, 0.02214941754937172])
(['wildlife trafficking', 'not wildlife trafficking'], [0.5210820436477661, 0.09291212260723114])
(['wildlife trafficking', 'not wildlife trafficking'], [0.6523442268371582, 0.06401912868022919])
(['not wildlife trafficking', 'wildlife trafficking'], [0.04799552634358406, 0.01685340516269207])
(['wildlif

In [70]:
lst1[:5]

[(['wildlife trafficking', 'not wildlife trafficking'],
  [0.25968116521835327, 0.012058272026479244]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.0990157499909401, 0.039518970996141434]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.0292100477963686, 0.009051206521689892]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.1545344889163971, 0.04707414284348488]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.08096851408481598, 0.03361132740974426])]

In [71]:
lst2=[]
for i in range(1000,2000):
    tupped1=classify_text(lst[i])
    print(tupped1)
    lst2.append(tupped1)

(['wildlife trafficking', 'not wildlife trafficking'], [0.013623729348182678, 0.004250502213835716])
(['wildlife trafficking', 'not wildlife trafficking'], [0.24816808104515076, 0.04450336843729019])
(['not wildlife trafficking', 'wildlife trafficking'], [0.02502208761870861, 0.013406828045845032])
(['wildlife trafficking', 'not wildlife trafficking'], [0.22741548717021942, 0.02721005119383335])
(['not wildlife trafficking', 'wildlife trafficking'], [0.04078982397913933, 0.019644159823656082])
(['wildlife trafficking', 'not wildlife trafficking'], [0.45581528544425964, 0.06844024360179901])
(['wildlife trafficking', 'not wildlife trafficking'], [0.1426595002412796, 0.06754422187805176])
(['wildlife trafficking', 'not wildlife trafficking'], [0.25854262709617615, 0.08676613122224808])
(['not wildlife trafficking', 'wildlife trafficking'], [0.02337004616856575, 0.0050648958422243595])
(['wildlife trafficking', 'not wildlife trafficking'], [0.8621530532836914, 0.001229342888109386])
(['no

In [72]:
lst2[:5]

[(['wildlife trafficking', 'not wildlife trafficking'],
  [0.013623729348182678, 0.004250502213835716]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.24816808104515076, 0.04450336843729019]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.02502208761870861, 0.013406828045845032]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.22741548717021942, 0.02721005119383335]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.04078982397913933, 0.019644159823656082])]

In [73]:
lst3=[]
for i in range(2000,3000):
    tupped2=classify_text(lst[i])
    print(tupped2)
    lst3.append(tupped2)

(['not wildlife trafficking', 'wildlife trafficking'], [0.018541621044278145, 0.013608645647764206])
(['wildlife trafficking', 'not wildlife trafficking'], [0.21778587996959686, 0.08978106826543808])
(['wildlife trafficking', 'not wildlife trafficking'], [0.3777705729007721, 0.30274587869644165])
(['wildlife trafficking', 'not wildlife trafficking'], [0.0774054229259491, 0.05259564891457558])
(['not wildlife trafficking', 'wildlife trafficking'], [0.1570267379283905, 0.07625801116228104])
(['wildlife trafficking', 'not wildlife trafficking'], [0.5085254907608032, 0.013806954026222229])
(['not wildlife trafficking', 'wildlife trafficking'], [0.19446039199829102, 0.12427514046430588])
(['wildlife trafficking', 'not wildlife trafficking'], [0.15649953484535217, 0.09770797938108444])
(['wildlife trafficking', 'not wildlife trafficking'], [0.9650033116340637, 0.0017020822269842029])
(['wildlife trafficking', 'not wildlife trafficking'], [0.2658938765525818, 0.21781452000141144])
(['not wild

In [74]:
lst3[:5]

[(['not wildlife trafficking', 'wildlife trafficking'],
  [0.018541621044278145, 0.013608645647764206]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.21778587996959686, 0.08978106826543808]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.3777705729007721, 0.30274587869644165]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.0774054229259491, 0.05259564891457558]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.1570267379283905, 0.07625801116228104])]

In [75]:
lst4=[]
for i in range(3000,4000):
    tupped3=classify_text(lst[i])
    print(tupped3)
    lst4.append(tupped3)

(['wildlife trafficking', 'not wildlife trafficking'], [0.6536250710487366, 0.02449723705649376])
(['wildlife trafficking', 'not wildlife trafficking'], [0.6325700879096985, 0.001651235856115818])
(['wildlife trafficking', 'not wildlife trafficking'], [0.4278965890407562, 0.01975283958017826])
(['wildlife trafficking', 'not wildlife trafficking'], [0.2675360441207886, 0.04006306827068329])
(['not wildlife trafficking', 'wildlife trafficking'], [0.04483361169695854, 0.021294645965099335])
(['wildlife trafficking', 'not wildlife trafficking'], [0.06302456557750702, 0.016829699277877808])
(['not wildlife trafficking', 'wildlife trafficking'], [0.08333844691514969, 0.05583196133375168])
(['wildlife trafficking', 'not wildlife trafficking'], [0.16264720261096954, 0.09672050178050995])
(['wildlife trafficking', 'not wildlife trafficking'], [0.06047318875789642, 0.03425392881035805])
(['wildlife trafficking', 'not wildlife trafficking'], [0.040535688400268555, 0.0336155891418457])
(['not wild

In [76]:
lst4[:5]

[(['wildlife trafficking', 'not wildlife trafficking'],
  [0.6536250710487366, 0.02449723705649376]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.6325700879096985, 0.001651235856115818]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.4278965890407562, 0.01975283958017826]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.2675360441207886, 0.04006306827068329]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.04483361169695854, 0.021294645965099335])]

In [77]:
lst5=[]
for i in range(4000,5000):
    tupped4=classify_text(lst[i])
    print(tupped4)
    lst5.append(tupped4)

(['wildlife trafficking', 'not wildlife trafficking'], [0.10802698135375977, 0.05338175594806671])
(['wildlife trafficking', 'not wildlife trafficking'], [0.7825445532798767, 0.4429624080657959])
(['not wildlife trafficking', 'wildlife trafficking'], [0.08678513020277023, 0.05510998144745827])
(['wildlife trafficking', 'not wildlife trafficking'], [0.17136205732822418, 0.06919000297784805])
(['not wildlife trafficking', 'wildlife trafficking'], [0.03466502204537392, 0.03383878245949745])
(['wildlife trafficking', 'not wildlife trafficking'], [0.43293434381484985, 0.031394392251968384])
(['wildlife trafficking', 'not wildlife trafficking'], [0.5475894808769226, 0.041438985615968704])
(['wildlife trafficking', 'not wildlife trafficking'], [0.02428719773888588, 0.01609473116695881])
(['not wildlife trafficking', 'wildlife trafficking'], [0.01965930312871933, 0.015926089137792587])
(['not wildlife trafficking', 'wildlife trafficking'], [0.07358330488204956, 0.009736970067024231])
(['wildli

In [78]:
lst5[:5]

[(['wildlife trafficking', 'not wildlife trafficking'],
  [0.10802698135375977, 0.05338175594806671]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.7825445532798767, 0.4429624080657959]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.08678513020277023, 0.05510998144745827]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.17136205732822418, 0.06919000297784805]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.03466502204537392, 0.03383878245949745])]

In [79]:
lst6=[]
for i in range(5000,6000):
    tupped5=classify_text(lst[i])
    print(tupped5)
    lst6.append(tupped5)

(['wildlife trafficking', 'not wildlife trafficking'], [0.2585431933403015, 0.10724838823080063])
(['not wildlife trafficking', 'wildlife trafficking'], [0.10643380135297775, 0.06865550577640533])
(['wildlife trafficking', 'not wildlife trafficking'], [0.9599823951721191, 0.0008643137407489121])
(['wildlife trafficking', 'not wildlife trafficking'], [0.9693505167961121, 0.00028990639839321375])
(['wildlife trafficking', 'not wildlife trafficking'], [0.9265215396881104, 0.0006420001736842096])
(['wildlife trafficking', 'not wildlife trafficking'], [0.34075412154197693, 0.17123043537139893])
(['wildlife trafficking', 'not wildlife trafficking'], [0.9149314761161804, 0.001009480794891715])
(['wildlife trafficking', 'not wildlife trafficking'], [0.9873848557472229, 0.002265801653265953])
(['wildlife trafficking', 'not wildlife trafficking'], [0.1818811148405075, 0.012516395188868046])
(['not wildlife trafficking', 'wildlife trafficking'], [0.03181352838873863, 0.017007118090987206])
(['not

In [80]:
lst6[:5]

[(['wildlife trafficking', 'not wildlife trafficking'],
  [0.2585431933403015, 0.10724838823080063]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.10643380135297775, 0.06865550577640533]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.9599823951721191, 0.0008643137407489121]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.9693505167961121, 0.00028990639839321375]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.9265215396881104, 0.0006420001736842096])]

In [82]:
lst7=[]
for i in range(6000,6790):
    tupped6=classify_text(lst[i])
    print(tupped6)
    lst7.append(tupped6)

(['wildlife trafficking', 'not wildlife trafficking'], [0.21217167377471924, 0.08138364553451538])
(['wildlife trafficking', 'not wildlife trafficking'], [0.17321555316448212, 0.0016834338894113898])
(['wildlife trafficking', 'not wildlife trafficking'], [0.5130783319473267, 0.006187145598232746])
(['not wildlife trafficking', 'wildlife trafficking'], [0.04191058129072189, 0.006893218960613012])
(['wildlife trafficking', 'not wildlife trafficking'], [0.12380217015743256, 0.01252945140004158])
(['wildlife trafficking', 'not wildlife trafficking'], [0.06039631739258766, 0.04038658365607262])
(['not wildlife trafficking', 'wildlife trafficking'], [0.024970941245555878, 0.003534192917868495])
(['wildlife trafficking', 'not wildlife trafficking'], [0.8665106296539307, 0.004800890106707811])
(['not wildlife trafficking', 'wildlife trafficking'], [0.92374187707901, 0.5361048579216003])
(['wildlife trafficking', 'not wildlife trafficking'], [0.10937727987766266, 0.041344475001096725])
(['wildl

In [83]:
lst7[:5]

[(['wildlife trafficking', 'not wildlife trafficking'],
  [0.21217167377471924, 0.08138364553451538]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.17321555316448212, 0.0016834338894113898]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.5130783319473267, 0.006187145598232746]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.04191058129072189, 0.006893218960613012]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.12380217015743256, 0.01252945140004158])]

In [86]:
lst_score_label=lst1+lst2+lst3+lst4+lst5+lst6+lst7
lst_score_label

[(['wildlife trafficking', 'not wildlife trafficking'],
  [0.25968116521835327, 0.012058272026479244]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.0990157499909401, 0.039518970996141434]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.0292100477963686, 0.009051206521689892]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.1545344889163971, 0.04707414284348488]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.08096851408481598, 0.03361132740974426]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.25151917338371277, 0.018917076289653778]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.022322705015540123, 0.02214941754937172]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.5210820436477661, 0.09291212260723114]),
 (['wildlife trafficking', 'not wildlife trafficking'],
  [0.6523442268371582, 0.06401912868022919]),
 (['not wildlife trafficking', 'wildlife trafficking'],
  [0.047995526343

In [89]:
df_rep_cleaned.loc[:, 'labels and scores']=lst_score_label
df_rep_cleaned.head()

name  \
1     Morgan Smith   
3      Sarah Perez   
17     Jeff Wright   
19   Michael Kelly   
22  Michael Bishop   

                                                                                                                                              url  \
1                          https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3   https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
17                                                https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
19                                                  https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
22                                             https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              relevant_content  \
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [97]:
lst_labels=[]
lst_scores=[]
for i in df_rep_cleaned['labels and scores']:
    label_vals=i[0]
    score_val=i[1]
    lst_labels.append(label_vals)
    lst_scores.append(score_val)

In [98]:
lst_labels[:5]

[['wildlife trafficking', 'not wildlife trafficking'],
 ['not wildlife trafficking', 'wildlife trafficking'],
 ['wildlife trafficking', 'not wildlife trafficking'],
 ['wildlife trafficking', 'not wildlife trafficking'],
 ['not wildlife trafficking', 'wildlife trafficking']]

In [99]:
lst_scores[:5]

[[0.25968116521835327, 0.012058272026479244],
 [0.0990157499909401, 0.039518970996141434],
 [0.0292100477963686, 0.009051206521689892],
 [0.1545344889163971, 0.04707414284348488],
 [0.08096851408481598, 0.03361132740974426]]

In [101]:
df_rep_cleaned_ls=df_rep_cleaned.copy()
df_rep_cleaned_ls.loc[:, 'label']=lst_labels
df_rep_cleaned_ls.head()

name  \
1     Morgan Smith   
3      Sarah Perez   
17     Jeff Wright   
19   Michael Kelly   
22  Michael Bishop   

                                                                                                                                              url  \
1                          https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3   https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
17                                                https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
19                                                  https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
22                                             https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              relevant_content  \
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [102]:
df_rep_cleaned_ls.loc[:, 'score']=lst_scores
df_rep_cleaned_ls.head()

name  \
1     Morgan Smith   
3      Sarah Perez   
17     Jeff Wright   
19   Michael Kelly   
22  Michael Bishop   

                                                                                                                                              url  \
1                          https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3   https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
17                                                https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
19                                                  https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
22                                             https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              relevant_content  \
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [103]:
#df_rep_cleaned_ls.to_json('rows_scores_labels_sep.json',orient='records',lines=True)

In [90]:
#df_rep_cleaned.to_json('seven_k_rows_scores_labels.json', orient='records', lines=True)

In [105]:
lst_final_label=[]
for i in df_rep_cleaned_ls['label']:
    lst_final_label.append(i[0])

In [107]:
df_rep_cleaned_ls['final label']=lst_final_label
df_rep_cleaned_ls

name  \
1        Morgan Smith   
3         Sarah Perez   
17        Jeff Wright   
19      Michael Kelly   
22     Michael Bishop   
...               ...   
31261   Matthew Scott   
31262    Nancy Willis   
31264   Matthew Scott   
31266    Joseph Greer   
31267     James Brown   

                                                                                                                                                     url  \
1                                 https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3          https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
17                                                       https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
19                                                         https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
22                                                    https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   
...                                                                                                                                                  ...   
31261                                                              https://www.nationaltribune.com.au/wa-man-jailed-after-3kg-of-meth-found-in-backpack/   
31262                                             https://www.pressdemocrat.com/article/napa/napa-panel-addresses-artists-need-for-space-and-visibility/   
31264                                                                                    https://www.nytimes.com/2017/12/05/science/sumatran-tigers.html   
31266  https://cw39.com/news/local/watch-live-harris-county-sheriffs-office-us-marshals-capture-most-wanted-fugitive-charged-in-girlfriends-2006-murder/   
31267                                                          https://www.mirror.co.uk/news/world-news/fugitive-unimpressed-smiling-james-brown-7157557   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [108]:
lst_final_score=[]
for i in df_rep_cleaned_ls['score']:
    lst_final_score.append(i[0])

In [110]:
df_rep_cleaned_ls['final score']=lst_final_score
df_rep_cleaned_ls

name  \
1        Morgan Smith   
3         Sarah Perez   
17        Jeff Wright   
19      Michael Kelly   
22     Michael Bishop   
...               ...   
31261   Matthew Scott   
31262    Nancy Willis   
31264   Matthew Scott   
31266    Joseph Greer   
31267     James Brown   

                                                                                                                                                     url  \
1                                 https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
3          https://www.khq.com/news/gonzaga-nursing-student-releases-debut-single-love-lives-in-a-room/article_4819f334-8362-11ee-8d90-274d3a8e3f99.html   
17                                                       https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
19                                                         https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
22                                                    https://www.saltwire.com/atlantic-canada/news/cape-breton-court-report-for-july-15-2021-100612132/   
...                                                                                                                                                  ...   
31261                                                              https://www.nationaltribune.com.au/wa-man-jailed-after-3kg-of-meth-found-in-backpack/   
31262                                             https://www.pressdemocrat.com/article/napa/napa-panel-addresses-artists-need-for-space-and-visibility/   
31264                                                                                    https://www.nytimes.com/2017/12/05/science/sumatran-tigers.html   
31266  https://cw39.com/news/local/watch-live-harris-county-sheriffs-office-us-marshals-capture-most-wanted-fugitive-charged-in-girlfriends-2006-murder/   
31267                                                          https://www.mirror.co.uk/news/world-news/fugitive-unimpressed-smiling-james-brown-7157557   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [ ]:
import spacy
nlp = spacy.load('en_core_web_sm')
def extract_names(text):
    doc=nlp(text)
    names=[ent.text for ent in doc.ents if ent.label_ == "PERSON"]
    return names
df_rep_cleaned_ls['extracted_names'] = df_rep_cleaned_ls['relevant_content'].apply(extract_names)

In [ ]:
def check_involvement(text, names, keywords):
    involvement = {}
    if any(keyword in text for keyword in keywords):
        involvement[names] = "Potentially Involved"
    else:
        involvement[names] = "Not Involved"
    return involvement

keywords = ["poached", "trafficking", "illegal trade", 'animal poaching',"smuggling",'CITES violation','wildlife crime']
df_rep_cleaned_ls['name_involvement'] = df_rep_cleaned_ls.apply(lambda x: check_involvement(x['relevant_content'], x['name'], keywords), axis=1)


In [111]:
#df_rep_cleaned_ls.to_json('final_label_score_sep.json',orient='records',lines=True)

In [113]:
filter1=df_rep_cleaned_ls[df_rep_cleaned_ls['final label']=='wildlife trafficking']
filter1

name  \
1       Morgan Smith   
17       Jeff Wright   
19     Michael Kelly   
30       Tanya Smith   
37       Tanya Smith   
...              ...   
31237   Marie Hunter   
31254    James Lewis   
31257  Jerry Jackson   
31258  Jerry Jackson   
31267    James Brown   

                                                                                                                                                           url  \
1                                       https://slate.com/news-and-politics/2007/10/who-s-allowed-to-sell-a-venomous-snake-and-why-would-you-ever-buy-one.html   
17                                                             https://news.maryland.gov/dnr/2019/07/30/cambridge-angler-reels-in-record-mahi-near-ocean-city/   
19                                                               https://www.fox13news.com/sports/usf-ad-michael-kelly-taking-the-coaching-search-by-the-horns   
30                                                                                                https://freeweekly.com/2021/03/26/laughing-all-the-way-home/   
37                                               https://www.earthisland.org/journal/index.php/articles/entry/big-cat-public-safety-act-reintroduced-in-house/   
...                                                                                                                                                        ...   
31237                                                                                                https://www.richlandsource.com/2023/09/08/mildred-hunter/   
31254                                    https://nationalzoo.si.edu/news/smithsonian-scientists-find-deadly-pathogen-not-present-pet-salamanders-united-states   
31257  https://www.baltimoresun.com/2019/05/04/bald-eagle-poisoning-deaths-have-become-rare-across-us-but-not-in-a-part-of-maryland-dubbed-bald-eagle-central/   
31258     https://www.baltimoresun.com/2019/05/01/more-bald-eagles-found-dead-on-marylands-eastern-shore-as-authorities-struggle-to-solve-systemic-poisonings/   
31267                                                                https://www.mirror.co.uk/news/world-news/fugitive-unimpressed-smiling-james-brown-7157557   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

In [115]:
filter2=filter1[filter1['final score']>=0.5]
filter2

name  \
37        Tanya Smith   
45     Natalie Thomas   
289       Andrew Tate   
295       Andrew Tate   
302       Andrew Tate   
...               ...   
31087      Bill Clark   
31089      Bill Clark   
31090      Bill Clark   
31170      Jiang Jing   
31229      Chad Jones   

                                                                                                                          url  \
37              https://www.earthisland.org/journal/index.php/articles/entry/big-cat-public-safety-act-reintroduced-in-house/   
45                                                                               https://www.jpost.com/opinion/article-780703   
289                                               https://www.yahoo.com/entertainment/tiger-king-zoo-owner-doc-195014428.html   
295                                 https://www.dailystar.co.uk/news/world-news/first-trillionaire-andrew-tates-true-30283258   
302                                   https://www.wvnstv.com/news/ap-andrew-tate-sues-his-accusers-in-human-trafficking-case/   
...                                                                                                                       ...   
31087                                                             https://www.voanews.com/a/elephant-dna-18jun15/2827873.html   
31089                                              https://rollcall.com/2022/07/18/ndaa-a-magnet-for-far-reaching-amendments/   
31090  https://news.mongabay.com/2018/04/wildlife-trade-detective-samuel-wasser-receives-prestigious-albert-schweitzer-medal/   
31170                                         https://www.traffic.org/news/china-joins-ethiopia-to-address-ivory-trafficking/   
31229                   https://sanangelolive.com/news/crime/2023-09-03/illegal-migrants-trap-songbirds-gambling-competitions   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [116]:
#filter1.to_json('filter_on_wildlife_traffic.json',orient='records',lines=True)

In [117]:
#filter2.to_json('filter_with_thresh_0.5.json', orient='records',lines=True)

In [66]:
import json
df_final_filter=pd.read_json('final_filter.json',lines=True)
df_final_filter.head()

name  \
0   Cody Jackson   
1  David Mendoza   
2  Jason Holland   
3  Kristi Miller   
4    John Thomas   

                                                                                                                                                    url  \
0                                                https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                                    https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2                        https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
3                                 https://www.twincities.com/2020/10/19/anoka-county-sheriff-investigating-death-of-st-paul-man-found-in-wildlife-area/   
4  https://www.somerset-kentucky.com/news/local_news/burnside-fugitive-located-in-eubank-storage-unit/article_b8ddf884-8b51-5b87-8eb5-cf4e0c2e392f.html   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [67]:
df_final_filter.shape

(76, 4)

In [148]:
label1=['wildlife trafficking', 'human trafficking','drug trafficking','not wildlife trafficking']
def classify_text1(text):
    result=classifier(text, candidate_labels=label1,multi_label=True)
    predicted_labels=result['labels']
    scores=result['scores']
    return predicted_labels,scores
text1=df_final_filter['relevant_content']
result1=df_final_filter['relevant_content'].apply(lambda x: classify_text1(x))
df_final_filter['predicted_labels'],df_final_filter['scores']=zip(*result1)

In [149]:
df_final_filter.head()

name  \
0   Cody Jackson   
1  David Mendoza   
2  Jason Holland   
3  Kristi Miller   
4    John Thomas   

                                                                                                                                                    url  \
0                                                https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                                    https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2                        https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
3                                 https://www.twincities.com/2020/10/19/anoka-county-sheriff-investigating-death-of-st-paul-man-found-in-wildlife-area/   
4  https://www.somerset-kentucky.com/news/local_news/burnside-fugitive-located-in-eubank-storage-unit/article_b8ddf884-8b51-5b87-8eb5-cf4e0c2e392f.html   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [150]:
lst8=[]
for i in df_final_filter['predicted_labels']:
    lst8.append(i[0])
df_final_filter['label']=lst8
df_final_filter

name  \
0     Cody Jackson   
1    David Mendoza   
2    Jason Holland   
3    Kristi Miller   
4      John Thomas   
..             ...   
71    Jeremy Moore   
72    Travis Smith   
73  Jackie Stewart   
74    Michael Wood   
75   Jerry Jackson   

                                                                                                                                                     url  \
0                                                 https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                                     https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2                         https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
3                                  https://www.twincities.com/2020/10/19/anoka-county-sheriff-investigating-death-of-st-paul-man-found-in-wildlife-area/   
4   https://www.somerset-kentucky.com/news/local_news/burnside-fugitive-located-in-eubank-storage-unit/article_b8ddf884-8b51-5b87-8eb5-cf4e0c2e392f.html   
..                                                                                                                                                   ...   
71                           https://raptorpersecutionuk.org/2023/11/27/police-believe-satellite-tagged-golden-eagle-has-come-to-harm-in-south-scotland/   
72                                                                                                           https://flaglerlive.com/smith-lyft-motions/   
73                                                          https://www.dailyrecord.co.uk/news/scottish-news/scots-hunters-sadistic-voice-notes-28574547   
74                                                                                                              https://raptorpersecutionuk.org/2015/02/   
75  https://www.baltimoresun.com/2019/05/01/more-bald-eagles-found-dead-on-marylands-eastern-shore-as-authorities-struggle-to-solve-systemic-poisonings/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [151]:
lst9=[]
for i in df_final_filter['scores']:
    lst9.append(i[0])
df_final_filter['score']=lst9
df_final_filter

name  \
0     Cody Jackson   
1    David Mendoza   
2    Jason Holland   
3    Kristi Miller   
4      John Thomas   
..             ...   
71    Jeremy Moore   
72    Travis Smith   
73  Jackie Stewart   
74    Michael Wood   
75   Jerry Jackson   

                                                                                                                                                     url  \
0                                                 https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                                     https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2                         https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
3                                  https://www.twincities.com/2020/10/19/anoka-county-sheriff-investigating-death-of-st-paul-man-found-in-wildlife-area/   
4   https://www.somerset-kentucky.com/news/local_news/burnside-fugitive-located-in-eubank-storage-unit/article_b8ddf884-8b51-5b87-8eb5-cf4e0c2e392f.html   
..                                                                                                                                                   ...   
71                           https://raptorpersecutionuk.org/2023/11/27/police-believe-satellite-tagged-golden-eagle-has-come-to-harm-in-south-scotland/   
72                                                                                                           https://flaglerlive.com/smith-lyft-motions/   
73                                                          https://www.dailyrecord.co.uk/news/scottish-news/scots-hunters-sadistic-voice-notes-28574547   
74                                                                                                              https://raptorpersecutionuk.org/2015/02/   
75  https://www.baltimoresun.com/2019/05/01/more-bald-eagles-found-dead-on-marylands-eastern-shore-as-authorities-struggle-to-solve-systemic-poisonings/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [152]:
label_lst=[1,1,1,0,0,0,0,0,1,0,1,1,0,0,0,1,1,0,0,0,1,0,0,0,1,1,1,0,1,0,1,1,1,1,0,0,0,0,0,0,0,0,0,1,1,1,1,1,1,0,0,0,0,1,1,1,0,0,1,1,0,1,1,1,0,0,0,0,1,1,0,1,0,0,0,0]
lst_info=['Reporter','Wildlife Trafficker','Reporter','Reporter','Drug Trafficker','Not Involved','Human Trafficker','Drug Trafficker','Judge','Not Involved','Judge','Wildlife Trafficker','Drug Trafficker','Reporter','Reporter','Wildlife Trafficker','Wildlife Trafficker','Investigator','Investigator','Investigator','Wildlife Trafficker','Drug Trafficker','Drug Trafficker','Investigator','Wildlife Activist','Reporter','Wildlife Activist','Not Involved','Investigator','Region','Wildlife Trafficker','Wildlife Trafficker','Wildlife Trafficker','Wildlife Trafficker','Reporter','Drug Trafficker','Drug Trafficker','Researcher','Weapons Trafficker','Animal Cruelty','Not Involved','Human Trafficker','Reporter','Reporter','Reporter','Wildlife Trafficker','Wildlife Trafficker','Wildlife Trafficker','Investigator','Reporter','Not Involved','Human Trafficker','Not Involved','Wildlife Trafficker','Wildlife Trafficker','Not Involved','Drug Trafficker','Not Involved','Reporter','Investigator','Wildlife Hunter','Investigator','Investigator','Investigator','Reporter','Reporter','Not Involved','Not Involved','Wildlife Trafficker','Investigator','Not Involved','Reporter','Not Involved','Animal Cruelty','Animal Cruelty','Reporter']
df_final_filter['actual label']=label_lst
df_final_filter['person info']=lst_info
df_final_filter

name  \
0     Cody Jackson   
1    David Mendoza   
2    Jason Holland   
3    Kristi Miller   
4      John Thomas   
..             ...   
71    Jeremy Moore   
72    Travis Smith   
73  Jackie Stewart   
74    Michael Wood   
75   Jerry Jackson   

                                                                                                                                                     url  \
0                                                 https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                                     https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2                         https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
3                                  https://www.twincities.com/2020/10/19/anoka-county-sheriff-investigating-death-of-st-paul-man-found-in-wildlife-area/   
4   https://www.somerset-kentucky.com/news/local_news/burnside-fugitive-located-in-eubank-storage-unit/article_b8ddf884-8b51-5b87-8eb5-cf4e0c2e392f.html   
..                                                                                                                                                   ...   
71                           https://raptorpersecutionuk.org/2023/11/27/police-believe-satellite-tagged-golden-eagle-has-come-to-harm-in-south-scotland/   
72                                                                                                           https://flaglerlive.com/smith-lyft-motions/   
73                                                          https://www.dailyrecord.co.uk/news/scottish-news/scots-hunters-sadistic-voice-notes-28574547   
74                                                                                                              https://raptorpersecutionuk.org/2015/02/   
75  https://www.baltimoresun.com/2019/05/01/more-bald-eagles-found-dead-on-marylands-eastern-shore-as-authorities-struggle-to-solve-systemic-poisonings/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [153]:
fil1=df_final_filter[df_final_filter['actual label']==1]
fil1

name  \
0       Cody Jackson   
1      David Mendoza   
2      Jason Holland   
8      Henry Jackson   
10  Javier Caraballo   
11         Liu Cheng   
15   Vanessa Rondeau   
16     Preston Silva   
20   Roberto Cabrera   
24    Belinda Wright   
25         Peter Cox   
26     Julie Sherman   
28      Martin Green   
30           Lin Yun   
31     Gregory Logan   
32  Brett Williamson   
33  Erin Christensen   
43         John Ross   
44    Lauren Collins   
45     Joshua Taylor   
46     Joshua Taylor   
47         Yang Feng   
48      Brian Miller   
53           Qin Hua   
54  Michael Gonzalez   
55       David James   
58        Erik Ortiz   
59       Tara Wilson   
61       John Wilson   
62      Sarah Bailey   
63      Sarah Bailey   
68    William Howard   
69  Charles Davidson   
71      Jeremy Moore   

                                                                                                                                        url  \
0                                    https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                        https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2            https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
8                                                                                            http://news.bbc.co.uk/2/hi/uk_news/3313385.stm   
10             https://www.wionews.com/world/over-six-tonnes-of-shark-fins-seized-in-panama-five-arrested-in-illegal-trade-operation-615647   
11                                                https://www.newzimbabwe.com/seven-chinese-rhino-poaching-suspects-to-finally-stand-trial/   
15  https://www.localsyr.com/news/quebec-woman-arrested-and-charged-for-selling-smuggling-polar-bear-skulls-to-undercover-agent-in-buffalo/   
16         https://www.hindustantimes.com/india/kerala-cops-seize-ivory-of-40-tuskers-from-delhi-smuggler/story-U1xm0dGSUr2vxTMhVuK4rJ.html   
20                                           https://www.onegreenplanet.org/animalsandnature/animals-you-didnt-know-you-could-have-as-pets/   
24                                                       https://www.dtnext.in/edit/2022/04/28/the-mystery-of-kangaroos-turning-up-in-india   
25                                                                               https://www.mprnews.org/story/2015/03/31/smuggling-charges   
26                            https://news.mongabay.com/2022/11/indonesias-orangutans-declining-amid-lax-and-laissez-faire-law-enforcement/   
28                                          https://www.lincolnshirelive.co.uk/news/local-news/sheep-burned-alive-horrific-incident-4346107   
30                                       https://malawi24.com/2021/06/11/chinese-national-convicted-of-wildlife-crime-and-money-laundering/   
31                                                    https://www.cbc.ca/news/canada/new-brunswick/narwhal-smuggle-rcmp-logan-u-s-1.3495603   
32                                            https://www.the-journal.com/articles/nucla-men-tennessee-clients-busted-after-17-elk-poached/   
33                                           https://foxsanantonio.com/newsletter-daily/woman-who-brought-raccoon-to-faces-criminal-charges   
43                                             https://lostcoastoutpost.com/2018/mar/22/people-are-poaching-succulents-mendo-sea-cliffs-an/   
44                                                https://www.nelsonstar.com/news/1-arrested-for-trafficking-black-bear-parts-in-bc-5559567   
45   https://www.koco.com/article/former-oklahoma-city-zoo-employee-pleads-guilty-to-trafficking-of-endangered-galapagos-tortoises/35727682   
46   https://kfor.com/news/former-oklahoma-city-zoo-employee-sentenced-after-pleading-guilty-to-trafficking-endangered-galapagos-tortoises/   
47                           

In [154]:
fil1[fil1['label']=='wildlife trafficking']

name  \
0       Cody Jackson   
1      David Mendoza   
2      Jason Holland   
8      Henry Jackson   
10  Javier Caraballo   
11         Liu Cheng   
15   Vanessa Rondeau   
24    Belinda Wright   
25         Peter Cox   
26     Julie Sherman   
30           Lin Yun   
31     Gregory Logan   
32  Brett Williamson   
33  Erin Christensen   
43         John Ross   
44    Lauren Collins   
46     Joshua Taylor   
47         Yang Feng   
48      Brian Miller   
53           Qin Hua   
54  Michael Gonzalez   
58        Erik Ortiz   
61       John Wilson   
63      Sarah Bailey   
68    William Howard   
69  Charles Davidson   
71      Jeremy Moore   

                                                                                                                                        url  \
0                                    https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                        https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2            https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
8                                                                                            http://news.bbc.co.uk/2/hi/uk_news/3313385.stm   
10             https://www.wionews.com/world/over-six-tonnes-of-shark-fins-seized-in-panama-five-arrested-in-illegal-trade-operation-615647   
11                                                https://www.newzimbabwe.com/seven-chinese-rhino-poaching-suspects-to-finally-stand-trial/   
15  https://www.localsyr.com/news/quebec-woman-arrested-and-charged-for-selling-smuggling-polar-bear-skulls-to-undercover-agent-in-buffalo/   
24                                                       https://www.dtnext.in/edit/2022/04/28/the-mystery-of-kangaroos-turning-up-in-india   
25                                                                               https://www.mprnews.org/story/2015/03/31/smuggling-charges   
26                            https://news.mongabay.com/2022/11/indonesias-orangutans-declining-amid-lax-and-laissez-faire-law-enforcement/   
30                                       https://malawi24.com/2021/06/11/chinese-national-convicted-of-wildlife-crime-and-money-laundering/   
31                                                    https://www.cbc.ca/news/canada/new-brunswick/narwhal-smuggle-rcmp-logan-u-s-1.3495603   
32                                            https://www.the-journal.com/articles/nucla-men-tennessee-clients-busted-after-17-elk-poached/   
33                                           https://foxsanantonio.com/newsletter-daily/woman-who-brought-raccoon-to-faces-criminal-charges   
43                                             https://lostcoastoutpost.com/2018/mar/22/people-are-poaching-succulents-mendo-sea-cliffs-an/   
44                                                https://www.nelsonstar.com/news/1-arrested-for-trafficking-black-bear-parts-in-bc-5559567   
46   https://kfor.com/news/former-oklahoma-city-zoo-employee-sentenced-after-pleading-guilty-to-trafficking-endangered-galapagos-tortoises/   
47                                                    https://www.cnn.com/2015/10/09/africa/tanzania-elephant-ivory-queen-arrest/index.html   
48               https://alaskapublic.org/2015/03/02/3000-pounds-of-auctioned-antlers-highlight-states-role-combating-wildlife-trafficking/   
53                                                        https://malawi24.com/2020/07/05/us-hails-conviction-of-chinese-citizen-in-malawi/   
54                                              https://www.nyasatimes.com/police-arrest-us-deputy-ambassador-malawi-found-smuggling-ivory/   
58                      https://www.nydailynews.com/2012/05/09/cuddly-yet-deadly-slow-lorises-are-abused-as-part-of-asias-exotic-pet-trade/   
61                                                http

In [155]:
fil2=df_final_filter[df_final_filter['actual label']==0]
fil2

name  \
3      Kristi Miller   
4        John Thomas   
5      Kelly Simmons   
6        Bryan White   
7      Andrew Miller   
9     William Murphy   
12     Jonathan Diaz   
13   Joseph Erickson   
14  Andrew Schneider   
17       Mark Powell   
18       Mark Powell   
19       Mark Powell   
21   Richard Garrett   
22    Angela Calhoun   
23      John Simpson   
27   Amanda Whitaker   
29      Norman Wells   
34         Amy Brady   
35     Daniel Powell   
36         Mark Lane   
37       Thomas Gray   
38   Julian Santiago   
39    Kristen Cooper   
40    Samantha Brown   
41        John Brown   
42         John Ross   
49      Adam Vaughan   
50     Andrew Harper   
51      Robert James   
52      Brian Nelson   
56         Tammy Lee   
57  Travis Maldonado   
60      Kurt Johnson   
64      Aaron Vaughn   
65      Mark Watkins   
66        John Mason   
67     Denise Harris   
70  William Campbell   
72      Travis Smith   
73    Jackie Stewart   
74      Michael Wood   
75     Jerry Jackson   

                                                                                                                                                                                     url  \
3                                                                  https://www.twincities.com/2020/10/19/anoka-county-sheriff-investigating-death-of-st-paul-man-found-in-wildlife-area/   
4                                   https://www.somerset-kentucky.com/news/local_news/burnside-fugitive-located-in-eubank-storage-unit/article_b8ddf884-8b51-5b87-8eb5-cf4e0c2e392f.html   
5                                         https://wpde.com/news/local/pent-house-crown-reef-beach-resort-and-waterpark-myrtle-beach-south-carolina-vacation-largest-resorts-grand-strand   
6                                                                          https://www.dispatch.ug/2021/05/08/ugandan-parliament-calls-for-prosecution-of-brian-white-over-sexual-abuse/   
7                                https://www.goldcoastbulletin.com.au/news/crime-court/drama-on-the-m1-an-alleged-stolen-car-spiked-at-tugun/news-story/164f3bcb93a9ad1af51499cc599f04ec   
9                                                                                     https://www.farmersjournal.ie/news/news/westmeath-farmer-fined-2-000-for-putting-in-a-drain-727828   
12                                                                                   http://homenewshere.com/tewksbury_town_crier/news/article_22c8e2fa-8b7f-11e4-aa3c-2b8156afc944.html   
13                                                                                  https://news4sanantonio.com/news/local/florida-sends-more-than-50-law-enforcement-officers-to-border   
14                                            https://www.houstonpublicmedia.org/articles/news/2017/12/29/257989/for-next-week-waugh-bat-colony-decimated-by-harvey-faces-slow-recovery/   
17                                                                                 https://nation.cymru/news/monmouthshire-man-prosecuted-for-destruction-of-protected-wildlife-habitat/   
18                                                                                            https://nation.cymru/news/company-fined-for-demolition-of-building-containing-a-bat-roost/   
19                                                                                 https://www.southwalesargus.co.uk/news/23395842.monmouthshire-topsoil-firm-court-newt-habitat-damage/   
21                               https://www.chronicleonline.com/news/local/lecanto-man-arrested-for-trafficking-meth-during-hurricane/article_78d8b6b3-371c-55a9-b493-82fb4d6bf6a2.html   
22                                                                                       https://okcfox.com/news/local/dhs-worker-under-investigation-for-smuggling-contraband-into-jail   
23                                                                                        https://www.helensburghadvertiser.co.uk/news/17727693.archive-hour-coulpo

In [156]:
fil2[fil2['label']=='wildlife trafficking']

name  \
3    Kristi Miller   
5    Kelly Simmons   
29    Norman Wells   
34       Amy Brady   
37     Thomas Gray   
49    Adam Vaughan   
52    Brian Nelson   
60    Kurt Johnson   
66      John Mason   
67   Denise Harris   
73  Jackie Stewart   
74    Michael Wood   
75   Jerry Jackson   

                                                                                                                                                     url  \
3                                  https://www.twincities.com/2020/10/19/anoka-county-sheriff-investigating-death-of-st-paul-man-found-in-wildlife-area/   
5         https://wpde.com/news/local/pent-house-crown-reef-beach-resort-and-waterpark-myrtle-beach-south-carolina-vacation-largest-resorts-grand-strand   
29                                          https://www.ctvnews.ca/canada/hunter-killed-by-bear-guide-survives-attack-in-northwest-territories-1.2013845   
34                                                     https://www.scientificamerican.com/article/the-troubling-mysteries-at-the-heart-of-nuclear-bombs/   
37                                                               https://www.voanews.com/a/myanmar-karen-state-wildlife-sanctuary-china-dam/3756828.html   
49                                                          https://www.theguardian.com/uk-news/2016/feb/18/national-wildlife-unit-to-close-within-weeks   
52                                                                                                https://cd.usembassy.gov/tag/fight-against-corruption/   
60                                                                                   https://witl.com/michigan-man-accused-of-killing-wolves-and-eagles/   
66                            https://raptorpersecutionuk.org/2024/01/11/wildlife-management-muirburn-bill-approaches-stage-2-cue-ridiculous-amendments/   
67                                                         https://www.businesspost.ie/news/trucking-firm-executive-fined-over-damage-to-local-wildlife/   
73                                                          https://www.dailyrecord.co.uk/news/scottish-news/scots-hunters-sadistic-voice-notes-28574547   
74                                                                                                              https://raptorpersecutionuk.org/2015/02/   
75  https://www.baltimoresun.com/2019/05/01/more-bald-eagles-found-dead-on-marylands-eastern-shore-as-authorities-struggle-to-solve-systemic-poisonings/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [157]:
df_final_filter[(df_final_filter['actual label']==1)&(df_final_filter['label']=='wildlife trafficking')]

name  \
0       Cody Jackson   
1      David Mendoza   
2      Jason Holland   
8      Henry Jackson   
10  Javier Caraballo   
11         Liu Cheng   
15   Vanessa Rondeau   
24    Belinda Wright   
25         Peter Cox   
26     Julie Sherman   
30           Lin Yun   
31     Gregory Logan   
32  Brett Williamson   
33  Erin Christensen   
43         John Ross   
44    Lauren Collins   
46     Joshua Taylor   
47         Yang Feng   
48      Brian Miller   
53           Qin Hua   
54  Michael Gonzalez   
58        Erik Ortiz   
61       John Wilson   
63      Sarah Bailey   
68    William Howard   
69  Charles Davidson   
71      Jeremy Moore   

                                                                                                                                        url  \
0                                    https://apnews.com/article/parrot-trafficking-florida-central-america-ec0419765166da98dbc94593d9c1654f   
1                                        https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
2            https://www.seafoodsource.com/news/supply-trade/seafood-salesman-convicted-of-smuggling-usd-68-million-of-eels-through-britain   
8                                                                                            http://news.bbc.co.uk/2/hi/uk_news/3313385.stm   
10             https://www.wionews.com/world/over-six-tonnes-of-shark-fins-seized-in-panama-five-arrested-in-illegal-trade-operation-615647   
11                                                https://www.newzimbabwe.com/seven-chinese-rhino-poaching-suspects-to-finally-stand-trial/   
15  https://www.localsyr.com/news/quebec-woman-arrested-and-charged-for-selling-smuggling-polar-bear-skulls-to-undercover-agent-in-buffalo/   
24                                                       https://www.dtnext.in/edit/2022/04/28/the-mystery-of-kangaroos-turning-up-in-india   
25                                                                               https://www.mprnews.org/story/2015/03/31/smuggling-charges   
26                            https://news.mongabay.com/2022/11/indonesias-orangutans-declining-amid-lax-and-laissez-faire-law-enforcement/   
30                                       https://malawi24.com/2021/06/11/chinese-national-convicted-of-wildlife-crime-and-money-laundering/   
31                                                    https://www.cbc.ca/news/canada/new-brunswick/narwhal-smuggle-rcmp-logan-u-s-1.3495603   
32                                            https://www.the-journal.com/articles/nucla-men-tennessee-clients-busted-after-17-elk-poached/   
33                                           https://foxsanantonio.com/newsletter-daily/woman-who-brought-raccoon-to-faces-criminal-charges   
43                                             https://lostcoastoutpost.com/2018/mar/22/people-are-poaching-succulents-mendo-sea-cliffs-an/   
44                                                https://www.nelsonstar.com/news/1-arrested-for-trafficking-black-bear-parts-in-bc-5559567   
46   https://kfor.com/news/former-oklahoma-city-zoo-employee-sentenced-after-pleading-guilty-to-trafficking-endangered-galapagos-tortoises/   
47                                                    https://www.cnn.com/2015/10/09/africa/tanzania-elephant-ivory-queen-arrest/index.html   
48               https://alaskapublic.org/2015/03/02/3000-pounds-of-auctioned-antlers-highlight-states-role-combating-wildlife-trafficking/   
53                                                        https://malawi24.com/2020/07/05/us-hails-conviction-of-chinese-citizen-in-malawi/   
54                                              https://www.nyasatimes.com/police-arrest-us-deputy-ambassador-malawi-found-smuggling-ivory/   
58                      https://www.nydailynews.com/2012/05/09/cuddly-yet-deadly-slow-lorises-are-abused-as-part-of-asias-exotic-pet-trade/   
61                                                http

In [86]:
import spacy
nlp = spacy.load('en_core_web_sm')
def extract_names(text):
    doc=nlp(text)
    names=[ent.text for ent in doc.ents if ent.label_ == "PERSON"]
    return names
df_final_filter['extracted_names'] = df_final_filter['relevant_content'].apply(extract_names)

In [159]:
def check_involvement(text, names, keywords):
    involvement = {}
    if any(keyword in text for keyword in keywords):
        involvement[names] = "Potentially Involved"
    else:
        involvement[names] = "Not Involved"
    return involvement

keywords = ["poached", "trafficking", "illegal trade", 'animal poaching',"smuggling",'CITES violation','wildlife crime']
df_final_filter['name_involvement'] = df_final_filter.apply(lambda x: check_involvement(x['relevant_content'], x['name'], keywords), axis=1)


In [160]:
#df_final_filter.to_json('task3_tentative.json',orient='records',lines=True)

In [161]:
df_final_filter[df_final_filter['person info']=='Wildlife Trafficker']

name  \
1      David Mendoza   
11         Liu Cheng   
15   Vanessa Rondeau   
16     Preston Silva   
20   Roberto Cabrera   
30           Lin Yun   
31     Gregory Logan   
32  Brett Williamson   
33  Erin Christensen   
45     Joshua Taylor   
46     Joshua Taylor   
47         Yang Feng   
53           Qin Hua   
54  Michael Gonzalez   
68    William Howard   

                                                                                                                                        url  \
1                                        https://www.krqe.com/news/crime/tiger-cub-in-trailer-leads-to-federal-charges-for-albuquerque-man/   
11                                                https://www.newzimbabwe.com/seven-chinese-rhino-poaching-suspects-to-finally-stand-trial/   
15  https://www.localsyr.com/news/quebec-woman-arrested-and-charged-for-selling-smuggling-polar-bear-skulls-to-undercover-agent-in-buffalo/   
16         https://www.hindustantimes.com/india/kerala-cops-seize-ivory-of-40-tuskers-from-delhi-smuggler/story-U1xm0dGSUr2vxTMhVuK4rJ.html   
20                                           https://www.onegreenplanet.org/animalsandnature/animals-you-didnt-know-you-could-have-as-pets/   
30                                       https://malawi24.com/2021/06/11/chinese-national-convicted-of-wildlife-crime-and-money-laundering/   
31                                                    https://www.cbc.ca/news/canada/new-brunswick/narwhal-smuggle-rcmp-logan-u-s-1.3495603   
32                                            https://www.the-journal.com/articles/nucla-men-tennessee-clients-busted-after-17-elk-poached/   
33                                           https://foxsanantonio.com/newsletter-daily/woman-who-brought-raccoon-to-faces-criminal-charges   
45   https://www.koco.com/article/former-oklahoma-city-zoo-employee-pleads-guilty-to-trafficking-of-endangered-galapagos-tortoises/35727682   
46   https://kfor.com/news/former-oklahoma-city-zoo-employee-sentenced-after-pleading-guilty-to-trafficking-endangered-galapagos-tortoises/   
47                                                    https://www.cnn.com/2015/10/09/africa/tanzania-elephant-ivory-queen-arrest/index.html   
53                                                        https://malawi24.com/2020/07/05/us-hails-conviction-of-chinese-citizen-in-malawi/   
54                                              https://www.nyasatimes.com/police-arrest-us-deputy-ambassador-malawi-found-smuggling-ivory/   
68         https://www.elpasotimes.com/story/news/crime/2020/06/11/texas-living-rock-cactus-smuggling-ring-smuggled-rare-plants/5337580002/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [67]:
#df_final_filter.to_json('final_filter_scores.json', orient='records', lines=True)

In [79]:
df_final_filter1=df_final_filter[['name','url','relevant_content','actual label']]

In [81]:
#df_final_filter1.to_json('training_with_labels.json',orient='records', lines=True)